# Tutorial 2: Bellman equation, policy iteration and value iteration
Tutorials for course ECE1508 Reinforcement Learning at the University of Toronto.

Author: Yicheng (Eason) Qu

Email: eason.qu@mail.utoronto.ca

## The schedule of this tutorial
- Review of Bellman equation
- Validate the use of Bellman equation by deriving the value-state function
- Review of policy iteration and value iteration
- Show an example, and how these two methods work step by step
- Python script to implement methods


# ☕📚 Coffee vs. Library: A Simple Model-on RL Problem

We model the evening choices of a student as a **two-state Markov Decision Process**:

After finishing the last course of the day, you can two places to go:

- **State `s₀`: Coffee Shop**
  - **Action `a`: Buy coffee** → Reward = **2**, then go back to the Library (`s₁`).
  - **Action `b`: Linger at the shop** → Reward = **1**, stay at the Coffee Shop (`s₀`).

- **State `s₁`: Library**
  - **Action `a`: Study hard** → Reward = **1**, stay in the Library (`s₁`).
  - **Action `b`: Goof off** → Reward = **0**, drift back to the Coffee Shop (`s₀`).

---








## Definitions
Let policy $\pi$ be the preferred actions (distribution) at current state $s$. For example, $\pi(a|s)$ is the probability of selecting action $a$ at state $s$. Let the return be
$$
\large G_t=\sum_{k=0}^{\infty}\gamma^k R_{t+k+1}, \quad \gamma\in(0,1).
$$

- **State-value** under policy $\pi$:
$$
\large v_\pi(s)=\mathbb{E}_\pi\!\big[G_t \mid S_t=s\big]
$$

- **Action-value** under policy $\pi$:
$$
\large q_\pi(s,a)=\mathbb{E}_\pi\!\big[G_t \mid S_t=s,\;A_t=a\big]
$$

Equivalently, the recursive forms are expressed as followings (Bellman equations):
$$
\large
\begin{align}
&v_\pi(s)=\mathbb{E}_\pi\!\big[R_{t+1}+\gamma \mathbb{E}_{s_{t+1}}[v_\pi(s')]\mid S_t=s\big]= \mathbb{E}_\pi\big[R_{t+1}+\gamma\sum_{s'\in\mathcal{S}} v_\pi(s') p(s'|s_t) \big],\\
&q_\pi(s,a)
= \mathbb{E}_\pi\!\Big[
    R_{t+1}
    + \gamma \,
      \mathbb{E}_{a'\sim\pi(\cdot|S_{t+1})}
      \big[ q_\pi(S_{t+1},a') \big]
    \;\Big|\; S_t=s,\; A_t=a
\Big] = \mathbb{E}_\pi\!\Big[
    R_{t+1}
    + \gamma \sum_{s'\in\mathcal{S}} \;\; \underbrace{\sum_{a'\in\mathcal{A}} q_\pi(s',a')}_{v_\pi(s')} \;\; p(s'|s,a)
\Big].
\end{align}
$$

---

## Setup for Coffee vs Library problem, with decay factor $\gamma=0.9$

From $s_0$:
- action $a$: reward $2$, next $s_1$
- action $b$: reward $1$, next $s_0$

From $s_1$:
- action $a$: reward $1$, next $s_1$
- action $b$: reward $0$, next $s_0$






---

## Policy $\pi_a$: always choose $a$

#### Closed-form derivation
**Solving State-value functions (directly from the definition)**
- $$\large v_{\pi_a}(s_0) = 2 + \sum_{k=1}^\infty 0.9^k*1 = 2+\frac{0.9}{1-0.9} = 11$$
- $$\large v_{\pi_a}(s_1) = 1 + \sum_{k=1}^\infty 0.9^k*1 = 1+\frac{0.9}{1-0.9} = 10$$

**Action-value functions**
- $q_{\pi_a}(s_0,a)=2 + \sum_{k=1}^\infty 0.9^k*1 = 11$
- $q_{\pi_a}(s_0,b)=1+0.9*2+\sum_{k=2}^\infty 0.9^k*1 = 1+ 0.9*(2+\sum_{k=1}^\infty 0.9^k*1) = 1+0.9*v_{\pi_a}(s_0) = 10.9$
- $q_{\pi_a}(s_1,a) = 1 + \sum_{k=1}^\infty 0.9^k*1=10$
- $q_{\pi_a}(s_1,b)=0+0.9*(2+\sum_{k=1}^\infty 0.9^k*1) = 9.9$


#### Bellman equation derivation
**Bellman equations**
$$
\large v_{\pi_a}(s_0)=2+0.9\,v_{\pi_a}(s_1)
$$
$$
\large v_{\pi_a}(s_1)=1+0.9\,v_{\pi_a}(s_1)
$$


- $v_{\pi_a}(s_0)=2+0.9\times 10=11$
- $v_{\pi_a}(s_1)=\tfrac{1}{1-0.9}=10$


**Action-values**

Since the transition is deterministic, we can find the action-value function from $q_\pi(s,a)=r(s,a)+\gamma v_\pi(s')$

- $q_{\pi_a}(s_0,a)=2+0.9v_{\pi_a}(s_1) = 11$
- $q_{\pi_a}(s_0,b)=10.9$
- $q_{\pi_a}(s_1,a)=10$
- $q_{\pi_a}(s_1,b)=9.9$

 ## Policy $\pi_{ab}$: choose $a$ with probability $p_a$ and $b$ with $p_b=1-p_a$
#### Close form derivation
**Solving State-values**
- $$ {\LARGE v_{\pi_{ab}}(s_0) = \underbrace{2*p_a+1*p_b}_{\text{reward at t+1}} + \underbrace{0.9[p_a\underbrace{(p_a*1+p_b*0)}_{\text{in } s_1 \text{ at } t+2} + p_b\underbrace{(2*p_a+1*p_b)}_{\text{in } s_0 \text{ at } t+2} ]}_{\text{reward at t+2}} + 0.9^2\cdots}$$

#### Bellman equation derivation
**Bellman equations**
- $$ {\large v_{\pi_{ab}}(s_0) = \underbrace{2*p_a+1*p_b}_{\text{reward at t+1}} + 0.9*[p_a*v_{\pi_{ab}}(s_1)+p_b*v_{\pi_{ab}}(s_0)] = 2p_a+p_b+0.9p_a v_{\pi_{ab}}(s_1)+0.9p_bv_{\pi_{ab}}(s_0)} $$
- $$ {\large v_{\pi_{ab}}(s_1)  = p_a+0.9p_a v_{\pi_{ab}}(s_1)+0.9p_bv_{\pi_{ab}}(s_0)} $$

**Solving the the group of linear equations**
- $$v_{\pi_{ab}}(s_0) = \frac{9p_a^2+9p_ap_b-20p_a-10p_b}{9(p_a+p_b)-10} = p_a+10$$
- $$v_{\pi_{ab}}(s_1) = \frac{-9p_ap_b-10p_a-9p_b^2}{9(p_a+p_b)-10} = p_a+9$$

**Action-values**
- $q_{\pi_{ab}}(s_0,a) = 2+0.9(v_{\pi_{ab}}(s_1)) = 10.1+0.9p_a$
- $q_{\pi_{ab}}(s_0,b) = 1+0.9(v_{\pi_{ab}}(s_0)) = 10+0.9p_a$
- $q_{\pi_{ab}}(s_1,a) = 1+0.9(v_{\pi_{ab}}(s_1)) = 9.1+0.9p_a$
- $q_{\pi_{ab}}(s_1,b) = 0+0.9(v_{\pi_{ab}}(s_0)) = 9+0.9p_a$

## Policy Iteration Algorithm

**Input environment:**
- State space $\mathcal{S}$
- Action space $\mathcal{A}$
- Transition probabilities $P(s'|s,a)$
- Reward function $R(s,a)$
- Discount factor $\gamma \in (0,1)$

---

**Algorithm:**

1. Initialize policy $\pi$, state-value function $v_\pi(s)$.
2. **Repeat until convergence:**
   - **Policy Evaluation:**
     Compute the value function $v_\pi$ for the current policy $\pi$. Intuitively, this step answers *“If I follow my current policy, what long-term reward can I expect?”* by iteratively updating $v_\pi$ until stable.
        - Compute the expected rewards
            $$
               \large R_\pi(s) = \mathbb{E}_\pi[R(s,a)].
            $$
        - Iteratively update the state-value (**Solving Bellman equation**)
            $$ \large v_\pi^{\text{new}}(s) =  R_\pi(s) + \gamma \mathbb{E}[v_\pi(\bar{S})|s] = R_\pi(s) + \gamma \sum_{a\in\mathcal{A}}\sum_{s'\in\mathcal{S}} v_\pi(s')p(s'|s,a)\pi(a|s). $$
   - **Policy Improvement:**
     Improve the policy $\pi$ using the current value function $ v_\pi$. Intuitively, this step answers *“Given my current value estimates, which action is best in each state?”* by making $\pi$ greedy with respect to $v_\pi$.
        - Update the action-value function
        $$ \large q_\pi (s,a) = R(s,a) + \gamma\mathbb{E}_\pi[v_\pi(\bar{S})|s,a] $$
        - Choose the best action as the new policy
        $$ \large \pi(a|s) =\begin{cases} &1\;\; a  = \text{argmax } q_\pi(s,a),\\ &0\;\; a  \neq \text{argmax } q_\pi(s,a). \end{cases}  $$


   - **Termination:** if policy $\pi$ is unchanged (no further improvement possible), stop.



 ## Value Iteration Algorithm

**Input environment:**
- State space $\mathcal{S}$
- Action space $\mathcal{A}$
- Transition probabilities $P(s'|s,a)$
- Reward function $R(s,a)$
- Discount factor $\gamma \in (0,1)$

**Output:**
- Optimal policy $\pi^*$
- Optimal value function $V^*$

---

**Algorithm:**

1. Initialize state-value function $v_*(s)$.
2. **Repeat until convergence (max change $< \theta$):**
   - **Value Update (Bellman Optimality Backup):**
     At each iteration, update the value of every state directly using the **Bellman optimality equation**, with current optimal policy. Intuitively, this step answers *“If I act optimally from now on, what long-term reward can I expect starting in $s$?”
     $$
     \large v_*^{\text{new}}(s) \;=\; \max_{a \in \mathcal{A}}
     \Big[\underbrace{ R(s,a) + \gamma \sum_{s' \in \mathcal{S}} P(s'|s,a)\, v_*^{\text{old}}(s') }_{q_*(s,a)}\Big].
     $$

   - **Check Convergence:**
     Compute
     $$
     \Delta = \max_{s \in \mathcal{S}} \big| v^{\text{new}}(s) - v^{\text{old}}(s) \big|
     $$
     and stop if $\Delta$ is below certain threshold.

3. **Policy Extraction:**
   After convergence, derive the optimal policy by choosing the action that maximizes the expected return in each state:
   $$
   \large \pi(a|s) =\begin{cases} &1\;\; a  = \text{argmax } q_*(s,a),\\ &0\;\; a  \neq \text{argmax } q_*(s,a). \end{cases}
   $$


## Policy Iteration vs. Value Iteration

| Aspect | **Policy Iteration (PI)** | **Value Iteration (VI)** |
|--------|----------------------------|---------------------------|
| **Core Idea** | Iteratively **evaluate a policy** and then **improve it**. | Iteratively **update state values** using the Bellman optimality equation (acting as if optimal at every step). |
| **Policy Evaluation** | Solve/approximate the Bellman **expectation** equation for $\pi$. | Not explicit — value updates already use the optimality operator. |
| **Policy Improvement** | Explicit step: $\pi(s) \leftarrow \arg\max_a q_\pi(s,a)$. | Implicit in the $\max_a$ inside each backup. |
| **Update Rule** | $v_\pi(s) = \sum_a \pi(a|s)\Big[R(s,a) + \gamma \sum_{s'} P(s'|s,a)v_\pi(s')\Big]$ | $v(s) \leftarrow \max_a \Big[R(s,a) + \gamma \sum_{s'} P(s'|s,a)v(s')\Big]$ |
| **Termination** | Stop when $\pi$ no longer changes. | Stop when value changes $\Delta$ are below a threshold. |
| **Iterations** | Fewer but heavier (due to policy evaluation). | More but lighter (single backup per state). |
| **Output** | $\pi^*, v^*$ directly. | $v^*$ first, then derive $\pi^*$. |

---

**Summary:**
- PI = *evaluate a policy, then improve it*.
- VI = *update values directly via Bellman optimality*.
Both converge to the same $(\pi^*, v^*)$.


## Example: MDP with probablistic transition
- **State & Action space**
$$\mathcal{S} = \{s_0,s_1,s_2\},\;\;\;\mathcal{A} = \{a_0,a_1\}. $$

- **Reward Table**

$$
\begin{array}{c|c|c}
\text{State} & \text{Action} & \text{Reward} \\
\hline
s_0 & a_0 & 2.5 \\
s_0 & a_1 & 1.2 \\
s_1 & a_0 & 2.0 \\
s_1 & a_1 & 0.8 \\
s_2 & a_0 & 0.4 \\
s_2 & a_1 & -0.3 \\
\end{array}
$$
Alternatively, we can express this as the following vectors
$$r_{a_0}=\begin{bmatrix}2.5\\[2pt]2.0\\[2pt]0.4\end{bmatrix},\quad
r_{a_1}=\begin{bmatrix}1.2\\[2pt]0.8\\[2pt]-0.3\end{bmatrix},$$
- **Transition Table**
$$
\begin{array}{c c|c c c}
\text{Current state} & \text{Action} & \Pr(s' = s_0) & \Pr(s' = s_1) & \Pr(s' = s_2) \\
\hline
s_0 & a_0\  & 0 & 0.5 & 0.5 \\
s_0 & a_1\        & 0.7 & 0.3 & 0 \\
\hline
s_1 & a_0\     & 0 & 0.85 & 0.15 \\
s_1 & a_1\   & 0.6 & 0.3 & 0.1 \\
\hline
s_2 & a_0\     & 0 & 0 & 1.0 \\
s_2 & a_1\   & 0.4 & 0.4 & 0.2 \\
\end{array}
$$
Similarly, we can find the transition matrices on different actions
$$P_{a_0}=\begin{bmatrix}
0   & 0    & 0\\
0.5 & 0.85 & 0\\
0.5 & 0.15 & 1
\end{bmatrix},\quad
P_{a_1}=\begin{bmatrix}
0.7 & 0.6 & 0.4\\
0.3 & 0.3 & 0.4\\
0   & 0.1 & 0.2
\end{bmatrix}.
$$
Giving the convention that $s' = P_{a}s$ and $s$ is current state distribution and $s'$ is next state distribution.





---
### Policy iteration solution
- **Initialization**
    - policy and state-value function $$\pi_0(a|s) = \frac{1}{2}, \forall a\in\mathcal{A},s\in\mathcal{S},\;\;\; v_{\pi_0}(s) = 0, \forall s\in\mathcal{S}$$
    - transition matrices and rewards under policy $\pi_0$
        $$
P_{\pi_0}=\tfrac12\bigl( P_{a_0}+ P_{a_1}\bigr)
=
\begin{bmatrix}
0.35 & 0.30  & 0.20\\
0.40 & 0.575 & 0.20\\
0.25 & 0.125 & 0.60
\end{bmatrix},
\qquad
r_{\pi_0}=\tfrac12(r_{a_0}+r_{a_1})=
\begin{bmatrix}1.85\\[2pt]1.40\\[2pt]0.05\end{bmatrix}.
$$



- **Policy evaluation:**

Recall the state-value function is updated follow the Bellman equation:
$$
\large v_\pi^{\text{new}}(s) =  R_\pi(s) + \gamma \mathbb{E}[v_\pi^{\text{old}}(\bar{S})|s] = R_\pi(s) + \gamma \sum_{a\in\mathcal{A}}\sum_{s'\in\mathcal{S}} v_\pi(s')p(s'|s,a)\pi(a|s)
$$

Plug in our numbers, the state-value function for $v_{\pi_0}(s_0)$ can be obtained
$$\large
\begin{aligned}
v_{\pi_0}(s_0)
&=\tfrac12\Big[\,r(s_0,a_0)+\gamma\sum_{s'}p(s'|s_0,a_0)\,v_{\pi_0}(s')\Big]
+\tfrac12\Big[\,r(s_0,a_1)+\gamma\sum_{s'}p(s'|s_0,a_1)\,v_{\pi_0}(s')\Big]\\[4pt]
&=\tfrac12\Big[\,2.5+\gamma\big(0\cdot v_{\pi_0}(s_0)+0.5\,v_{\pi_0}(s_1)+0.5\,v_{\pi_0}(s_2)\big)\Big]\\
&\quad+\tfrac12\Big[\,1.2+\gamma\big(0.7\,v_{\pi_0}(s_0)+0.3\,v_{\pi_0}(s_1)+0\cdot v_{\pi_0}(s_2)\big)\Big].\\
\end{aligned}
$$
Hence we have $$ \large
v_{\pi_0}(s_0)=1.85+0.9\,(0.35\,v_{\pi_0}(s_0)+0.40\,v_{\pi_0}(s_1)+0.25\,v_{\pi_0}(s_2)).
$$
We can simplify the calculation using a matrix notation
$$
\large
\boxed{\,v_{\pi_0}^\top \;=\; r_{\pi_0}^\top \;+\; \gamma\, \underbrace{v_{\pi_0}^\top}_{*}\, P_{\pi_0}\,  }
$$
$*\text{value function at next state s'}$

In other words, we are solve the linear system
$$
\begin{aligned}
v_{\pi_0}(s_0)&=1.85+0.9\,(0.35\,v_{\pi_0}(s_0)+0.40\,v_{\pi_0}(s_1)+0.25\,v_{\pi_0}(s_2)),\\
v_{\pi_0}(s_1)&=1.40+0.9\,(0.30\,v_{\pi_0}(s_0)+0.575\,v_{\pi_0}(s_1)+0.125\,v_{\pi_0}(s_2)),\\
v_{\pi_0}(s_2)&=0.05+0.9\,(0.20\,v_{\pi_0}(s_0)+0.20\,v_{\pi_0}(s_1)+0.60\,v_{\pi_0}(s_2)).
\end{aligned}
$$

We have the solution
$$
\boxed{\,v_{\pi_0}(s_0)\approx 12.0162,\quad
v_{\pi_0}(s_1)\approx 11.8263,\quad
v_{\pi_0}(s_2)\approx 9.4384\, }.
$$



- **Policy improvement:**
    Recall we first update the action-value function:
$$ \large q_\pi (s,a) = R(s,a) + \gamma\mathbb{E}_\pi[v_\pi(\bar{S})|s,a]$$
    - At state $s_0$
            $$\begin{cases} q_{\pi_0}(s_0,a_0)=2.5+0.9\,[\,0.5\,v_{\pi_0}(s_1)+0.5\,v_{\pi_0}(s_2)\,]
=2.5+0.9\,[0.5\cdot 11.8263+0.5\cdot 9.4384]
\approx \mathbf{12.0691}.\\
q_{\pi_0}(s_0,a_1)=1.2+0.9\,[\,0.7\,v_{\pi_0}(s_0)+0.3\,v_{\pi_0}(s_1)\,]
=1.2+0.9\,[0.7\cdot 12.0162+0.3\cdot 11.8263]
\approx 11.9633.  \end{cases} $$
    *Hence the best policy at $s_0$ is choosing action $a_0$*
    - At state $s_1$
        $$\begin{cases}
q_{\pi_0}(s_1,a_0)=2.0+0.9\,[\,0.85\,v_{\pi_0}(s_1)+0.15\,v_{\pi_0}(s_2)\,]
=2.0+0.9\,[0.85\cdot 11.8263+0.15\cdot 9.4384]
\approx \mathbf{12.3213}\\
q_{\pi_0}(s_1,a_1)=0.8+0.9\,[\,0.6\,v_{\pi_0}(s_0)+0.3\,v_{\pi_0}(s_1)+0.1\,v_{\pi_0}(s_2)\,]
\approx 11.3313. \end{cases} $$
    *Hence the best policy at $s_1$ is choosing action $a_0$*
    - At state $s_2$
        $$ \begin{cases}
q_{\pi_0}(s_2,a_0)=0.4+0.9\,v_{\pi_0}(s_2)
=0.4+0.9\cdot 9.4384
\approx 8.8946\\ q_{\pi_0}(s_2,a_1)=-0.3+0.9\,[\,0.4\,v_{\pi_0}(s_0)+0.4\,v_{\pi_0}(s_1)+0.2\,v_{\pi_0}(s_2)\,]
\approx \mathbf{9.9822} \end{cases} $$
    *Hence the best policy at $s_2$ is choosing action $a_1$*

- **Update to next round**

  The new policy is $$\pi_1(s) = \begin{cases} a_0, \text{if } s=s_0,s_1,\\ a_1, \text{if } s=s_2. \end{cases}$$
  We start a new round until the policy converges

---
### Value iteration solution
- **Initialization**
$$
v_0(s)=0,\ \forall s\in\{s_0,s_1,s_2\},\qquad \gamma=0.9.
$$

- **Bellman optimality update**
$$
\large v_*^{\text{new}}(s) \;=\; \max_{a \in \mathcal{A}}
     \Big[\underbrace{ R(s,a) + \gamma \sum_{s' \in \mathcal{S}} P(s'|s,a)\, v_*^{\text{old}}(s') }_{q_*(s,a)}\Big].
$$

Since $v_0\equiv 0$, the expectation terms vanish and $q_0(s,a)=r(s,a)$.

- **Value update at round 1**

At state $s_0$
$$
q_0(s_0,a_0)=2.5,\qquad q_0(s_0,a_1)=1.2
\;\Rightarrow\;
v_1(s_0)=\max(2.5,1.2)=\boxed{2.5}.
$$

At state $s_1$
$$
q_0(s_1,a_0)=2.0,\qquad q_0(s_1,a_1)=0.8
\;\Rightarrow\;
v_1(s_1)=\max(2.0,0.8)=\boxed{2.0}.
$$

At state $s_2$
$$
q_0(s_2,a_0)=0.4,\qquad q_0(s_2,a_1)=-0.3
\;\Rightarrow\;
v_1(s_2)=\max(0.4,-0.3)=\boxed{0.4}.
$$

- **Value update at round 2**

We can also implement in matrix form
$$
\large
\mathbf{q}_1(a_0)=r_{a_0}+\gamma\, P_{a_0}^\top v_1,\qquad
\mathbf{q}_1(a_1)=r_{a_1}+\gamma\, P_{a_1}^\top v_1,
$$
where $\mathbf q_1(a)=
\begin{bmatrix} q_1(s_0,a) \\q_1(s_1,a)\\q_1(s_2,a)\end{bmatrix}$

**Evaluate the products**
$$
P_{a_0}^\top v_1=
\begin{bmatrix}
0 & 0.5 & 0.5\\
0 & 0.85 & 0.15\\
0 & 0 & 1
\end{bmatrix}
\!\begin{bmatrix}2.5\\2.0\\0.4\end{bmatrix}
=
\begin{bmatrix}
1.2\\ 1.76\\ 0.4
\end{bmatrix},
\qquad
\Rightarrow\quad
\mathbf q_{a_0}=
\begin{bmatrix}2.5\\2.0\\0.4\end{bmatrix}
+0.9\begin{bmatrix}1.2\\1.76\\0.4\end{bmatrix}
=
\begin{bmatrix}\mathbf{3.58}\\ \mathbf{3.584}\\ 0.76\end{bmatrix}.
$$

$$
 P_{a_1}^\top v_1=
\begin{bmatrix}
0.7 & 0.3 & 0\\
0.6 & 0.3 & 0.1\\
0.4 & 0.4 & 0.2
\end{bmatrix}
\!\begin{bmatrix}2.5\\2.0\\0.4\end{bmatrix}
=
\begin{bmatrix}
2.35\\ 2.14\\ 1.88
\end{bmatrix},
\qquad
\Rightarrow\quad
\mathbf q_{a_1}=
\begin{bmatrix}1.2\\0.8\\-0.3\end{bmatrix}
+0.9\begin{bmatrix}2.35\\2.14\\1.88\end{bmatrix}
=
\begin{bmatrix}3.315\\ 2.726\\ \mathbf{1.392}\end{bmatrix}.
$$

**Elementwise maximization**
$$
v_2=\max\!\big(\mathbf q_{a_0},\,\mathbf q_{a_1}\big)
=
\boxed{\begin{bmatrix}3.58\\ 3.584\\ 1.392\end{bmatrix}},
\qquad
\text{greedy policy at round 2}=\boxed{(a_0,\ a_0,\ a_1)}.
$$



---
## Python implementation
#### environment setup

In [11]:
import gymnasium as gym
import numpy as np
from gym import spaces

class ThreeStateMDPEnv(gym.Env):
    metadata = {"render_modes": ["ansi"], "render_fps": 0}

    def __init__(self, render_mode=None):
        super().__init__()
        # Observation: one of {0,1,2}
        self.observation_space = spaces.Discrete(3)
        # Action: a0=0, a1=1
        self.action_space = spaces.Discrete(2)

        #Transition matrices of different actions; s' = Ps, where s' is the next state
        self.P = np.array([
            # a0
            [[0.0, 0.5, 0.5],
             [0.0, 0.85, 0.15],
             [0.0, 0.0, 1.0]],
            # a1
            [[0.7, 0.3, 0.0],
             [0.6, 0.3, 0.1],
             [0.4, 0.4, 0.2]]
        ], dtype=np.float64)
        # Rewards r[a, s]
        self.R = np.array([
            [2.5, 2.0, 0.4],   # a0
            [1.2, 0.8, -0.3],  # a1
        ], dtype=np.float64)

        # Sanity check: rows sum to 1 (row-stochastic by (s,a))
        assert np.allclose(self.P.sum(axis=2), 1.0), "Each (s,a) row must sum to 1."

        self._state = 0
        self._last_action = None
        self.render_mode = render_mode
        self._rng = np.random.default_rng()

    def seed(self, seed=None):  # for Gym compatibility
        self._rng = np.random.default_rng(seed)
        return [seed]

    def reset(self, *, seed=None, options=None):
        if seed is not None:
            self._rng = np.random.default_rng(seed)
        # Choose a start state (you can change this if you prefer fixed start)
        self._state = 0
        self._last_action = None
        obs = int(self._state)
        info = {}
        # Gymnasium returns (obs, info); Gym returns obs
        try:
            return obs, info
        except TypeError:  # pragma: no cover
            return obs

    def step(self, action):
        action = int(action)
        assert self.action_space.contains(action), "Invalid action."

        s = self._state
        # Sample next state from P[action, s, :]
        probs = self.P[action, s]
        s_next = int(self._rng.choice(3, p=probs))

        reward = float(self.R[action, s])
        terminated = False          # no absorbing terminal state in this MDP
        truncated = False           # use TimeLimit wrapper if you want finite episodes
        info = {}

        self._state = s_next
        self._last_action = action

        # Gymnasium returns (obs, reward, terminated, truncated, info)
        try:
            return int(self._state), reward, terminated, truncated, info
        except TypeError:  # Gym fallback: (obs, reward, done, info)
            done = terminated or truncated
            return int(self._state), reward, done, info

    def close(self):
        pass


#### Policy iteration solution

In [12]:
from numpy.linalg import solve

def Policy_enval(P, R, gamma, pi):
    """
    Evaluate a (possibly stochastic) stationary policy π given:
      P: shape (A, S, S), row-stochastic by (a, s, s')
      R: shape (A, S)
      pi: shape (S, A), pi[s,a] = π(a|s)
    Returns v: shape (S,)
    Solves: (I - γ P_π) v = r_π
    """
    S, A = pi.shape[0], pi.shape[1]
    # r_π[s] = Σ_a π[s,a] R[a,s]
    r_pi = (pi * R.T).sum(axis=1)  # shape (S,)

    # P_π[s,:] = Σ_a π[s,a] P[a,s,:]
    P_pi = np.vstack([
        sum(pi[s, a] * P[a, s, :] for a in range(A))
        for s in range(S)
    ])  # shape (S, S)

    # Linear solve
    v = solve(np.eye(S) - gamma * P_pi, r_pi)
    return v

def Policy_improv(P, R, gamma, v):
    """
    Greedy policy improvement:
      q(s,a) = R[a,s] + γ * P[a,s,:] @ v
    Returns deterministic π_new of shape (S, A).
    """
    A, S, _ = P.shape
    q = np.zeros((S, A))
    for s in range(S):
        for a in range(A):
            q[s, a] = R[a, s] + gamma * (P[a, s, :] @ v)
    a_star = np.argmax(q, axis=1)
    pi_new = np.zeros_like(q)
    for s in range(S):
        pi_new[s, a_star[s]] = 1.0
    return pi_new, q


def actions_of(pi_det, actions=("a0","a1")):
    """Return ['a0', 'a0', 'a1'] from a deterministic policy matrix pi_det (one-hot rows)."""
    return [actions[int(np.argmax(pi_det[s]))] for s in range(pi_det.shape[0])]


env = ThreeStateMDPEnv()
P, R, gamma = env.P, env.R, 0.9
states = ("s0","s1","s2")
actions = ("a0","a1")

# Initialization: π0 is uniform (stochastic), v0 zeros
pi = np.full((3, 2), 0.5)
v  = np.zeros(3)

print("Implementation of Policy Iteration")
print("--------------------------------")
for k in range(5):
    # Evaluate current policy π_k
    v = Policy_enval(P, R, gamma, pi)

    # Improve -> π_{k+1} (deterministic)
    pi_next, q = Policy_improv(P, R, gamma, v)
    a_list = actions_of(pi_next, actions)

    # Trace: show pure actions for each state, plus values just evaluated
    print(f"iter {k}:  π_next = [{states[0]}→{a_list[0]}, {states[1]}→{a_list[1]}, {states[2]}→{a_list[2]}]   "
          f"V = [s0:{v[0]:.6f}, s1:{v[1]:.6f}, s2:{v[2]:.6f}]")

    # Move to next policy
    pi = pi_next

# Final summary (optional)
a_star = actions_of(pi, actions)
print("\nAfter 5 steps:")
print(f"Policy: [{states[0]}→{a_star[0]}, {states[1]}→{a_star[1]}, {states[2]}→{a_star[2]}]")
print(f"V: [s0:{v[0]:.6f}, s1:{v[1]:.6f}, s2:{v[2]:.6f}]")

Implementation of Policy Iteration
--------------------------------
iter 0:  π_next = [s0→a0, s1→a0, s2→a1]   V = [s0:12.016218, s1:11.826315, s2:9.438382]
iter 1:  π_next = [s0→a0, s1→a0, s2→a1]   V = [s0:16.305846, s1:16.599335, s2:14.080323]
iter 2:  π_next = [s0→a0, s1→a0, s2→a1]   V = [s0:16.305846, s1:16.599335, s2:14.080323]
iter 3:  π_next = [s0→a0, s1→a0, s2→a1]   V = [s0:16.305846, s1:16.599335, s2:14.080323]
iter 4:  π_next = [s0→a0, s1→a0, s2→a1]   V = [s0:16.305846, s1:16.599335, s2:14.080323]

After 5 steps:
Policy: [s0→a0, s1→a0, s2→a1]
V: [s0:16.305846, s1:16.599335, s2:14.080323]


In [14]:
def value_eval_opt_act(P, R, gamma, v):
    A, S, _ = P.shape
    q = np.zeros((S, A), dtype=float)
    for s in range(S):
        for a in range(A):
            q[s, a] = R[a, s] + gamma * (P[a, s, :] @ v)
    a_star = np.argmax(q, axis=1)
    return q, a_star


def value_iter(K=5, gamma=0.9):
    env = ThreeStateMDPEnv()
    P, R = env.P, env.R
    S, A = 3, 2
    states = ("s0", "s1", "s2")
    actions = ("a0", "a1")

    # Initialization
    v = np.zeros(S, dtype=float)

    print("Implementation of Value Iteration")
    print("---------------------")
    print(f"Init: v0 = [s0:{v[0]:.6f}, s1:{v[1]:.6f}, s2:{v[2]:.6f}]")

    for k in range(K):
        # One-step lookahead using v_k
        q, a_star = value_eval_opt_act(P, R, gamma, v)

        # Bellman optimality update to get v_{k+1}
        v_new = q.max(axis=1)

        # Trace: show the greedy (pure) policy induced by v_k and the updated values v_{k+1}
        pol_str = f"{states[0]}→{actions[a_star[0]]}, {states[1]}→{actions[a_star[1]]}, {states[2]}→{actions[a_star[2]]}"
        print(f"iter {k}:  π_greedy = [{pol_str}]   "
              f"v_{k+1} = [s0:{v_new[0]:.6f}, s1:{v_new[1]:.6f}, s2:{v_new[2]:.6f}]")

        # Move to next values
        v = v_new

    # Optional final summary
    q_final, a_star_final = value_eval_opt_act(P, R, gamma, v)
    pol_final = f"{states[0]}→{actions[a_star_final[0]]}, {states[1]}→{actions[a_star_final[1]]}, {states[2]}→{actions[a_star_final[2]]}"
    print("\nAfter", K, "iterations:")
    print(f"π_greedy (final wrt v_{K}) = [{pol_final}]")
    print(f"v_{K} = [s0:{v[0]:.6f}, s1:{v[1]:.6f}, s2:{v[2]:.6f}]")


if __name__ == "__main__":
    # Example: run 5 iterations
    value_iter(K=20, gamma=0.9)

Implementation of Value Iteration
---------------------
Init: v0 = [s0:0.000000, s1:0.000000, s2:0.000000]
iter 0:  π_greedy = [s0→a0, s1→a0, s2→a0]   v_1 = [s0:2.500000, s1:2.000000, s2:0.400000]
iter 1:  π_greedy = [s0→a0, s1→a0, s2→a1]   v_2 = [s0:3.580000, s1:3.584000, s2:1.392000]
iter 2:  π_greedy = [s0→a0, s1→a0, s2→a1]   v_3 = [s0:4.739200, s1:4.929680, s2:2.529600]
iter 3:  π_greedy = [s0→a0, s1→a0, s2→a1]   v_4 = [s0:5.856676, s1:6.112701, s2:3.636125]
iter 4:  π_greedy = [s0→a0, s1→a0, s2→a1]   v_5 = [s0:6.886972, s1:7.167093, s2:4.663478]
iter 5:  π_greedy = [s0→a0, s1→a0, s2→a1]   v_6 = [s0:7.823757, s1:8.112396, s2:5.598889]
iter 6:  π_greedy = [s0→a0, s1→a0, s2→a1]   v_7 = [s0:8.670078, s1:8.961833, s2:6.444815]
iter 7:  π_greedy = [s0→a0, s1→a0, s2→a1]   v_8 = [s0:9.432992, s1:9.725852, s2:7.207555]
iter 8:  π_greedy = [s0→a0, s1→a0, s2→a1]   v_9 = [s0:10.120033, s1:10.413297, s2:7.894544]
iter 9:  π_greedy = [s0→a0, s1→a0, s2→a1]   v_10 = [s0:10.738528, s1:11.031936, s